## <center> B-spline surfaces</center>

This notebook illustrates how a B-spline surface, defined by two knot vectors and a matrix of control points, c, parameterized by
$$ s(u, v)=\sum_{i=0}^m\sum_{j=0}^n c_{ij}N_i^{pu}(u)N_j^{pv}(v),\quad  u\in[a,b], v\in[c,d]$$
is discretized and represented by BasicBSpline.jl, and ploted with PlotlyJS.jl.

BasicBSpline.jl docs: [https://hyrodium.github.io/BasicBSpline.jl/dev/](https://hyrodium.github.io/BasicBSpline.jl/dev/)

In [1]:
using BasicBSpline, PlotlyJS, Random
rng = Random.MersenneTwister(125);

WebIO._IJuliaInit()

In [2]:
function ctrl_polyhedron(ctrl:: Matrix{Vector{T}}) where T
    # defines the  surface control polyhedron
    # ctrl:  in Matrix of control points, [x, y, z];
    # returns the coordinates of the polyhedron edge ends
   V = Vector{T}[[], [], []]
   m, n = size(ctrl) 
    for i=1:m
        for j=1:n-1
            for k=1:3
            append!(V[k], [ctrl[i, j][k], ctrl[i,j+1][k]])
            end
        end 
        for k=1:3
            push!(V[k], NaN)
        end
    end     
    for j=1:n
        for i=1:m-1
            for k=1:3
                append!(V[k], [ctrl[i, j][k], ctrl[i+1,j][k]]) 
            end
        end
        for k=1:3
            push!(V[k], NaN)
        end
    end 
    return V
end 

function bspline_surf(SManifold; M=100, N=100)
    BSu, BSv =SManifold.bsplinespaces
    I1 = domain(BSu)
    a, b = extrema(I1)
    I2 = domain(BSv)
    c, d = extrema(I2)
    u = LinRange(a, b, M)
    v = LinRange(c, d, N)
    bsurf = Matrix{Vector{Float64}}(undef, M, N)
    for (i, s) in enumerate(u)
        for (j,t) in enumerate(v)
            bsurf[i, j] = SManifold(s, t)
        end    
    end
    V = reduce(vcat, bsurf);
    x = reshape(V[1:3:end], (M, N))
    y = reshape(V[2:3:end], (M, N))
    z = reshape(V[3:3:end], (M, N))
    return x, y, z        
end;    

function fig_layout(;width=600, height=600, aspect="data")
    return Layout(width=width, height=height, scene_aspectmode=aspect, font_size=11,
                 scene_camera_eye=attr(x=1.95, y=1.95, z=1))
end;

### B-spline surface of different degrees in u and v

The following surface is  defined by knot vectors with the property that the first and last  (pu+1), respectively (pv+1) coordinates are equal. This property ensures that the segments, incident at the corners of the control polyhedron, are tangent to the surface boundary curves.

In [3]:
pu = 2
knotu = pu*KnotVector(1,4) + KnotVector(1:4) #m =length(knotu)
pv = 3
knotv = pv*KnotVector(1,5) + KnotVector(1:5) #n= length(knotv)
BSu = BSplineSpace{pu}(knotu)
BSv = BSplineSpace{pv}(knotv)
#random ctrl points defined following the BasicBSpline author's idea    
rand_ctrl = [1.2*rand(rng, 3) for i in 1:dim(BSu), j in 1:dim(BSv)]
ctrl = [[2*i-6.5, 2*j-6.5, -2+3*rand(rng)] for i in 1:dim(BSu), j in 1:dim(BSv)] + rand_ctrl
S = BSplineManifold(ctrl,(BSu, BSv));
x, y, z = bspline_surf(S; M=75, N=100);
Xe, Ye, Ze = ctrl_polyhedron(ctrl);

In [4]:
fig1 = Plot([scatter3d(x=Xe, y=Ye, z=Ze, mode="markers+lines", marker_size=4, marker_color="#777777"),
            surface(x=x, y=y, z=z, colorbar_thickness=25, colorbar_len=0.65, 
            cmin=minimum(z)-1, cmax=maximum(z))],
            fig_layout(;width=700))

data: [
  "scatter3d with fields marker, mode, type, x, y, and z",
  "surface with fields cmax, cmin, colorbar, type, x, y, and z"
]

layout: "layout with fields font, height, margin, scene, template, and width"

Plot the surface without control polyhedron:

In [5]:
fig2 = Plot(fig1.data[2], fig_layout(;width=700))

data: [
  "surface with fields cmax, cmin, colorbar, type, x, y, and z"
]

layout: "layout with fields font, height, margin, scene, template, and width"

### B-spline surface defined by the same sequence of knots, knotu=knotv, and the same degree, pu=pv

In [6]:
p = 2
knot = p*KnotVector(1, 4) + KnotVector(1:4)
BS = BSplineSpace{p}(knot)
rand_ctrl = [1.2*rand(rng, 3) for i in 1:dim(BS), j in 1:dim(BS)]
ctrl = [[2*i-6.5, 2*j-6.5, -2+3*rand(rng)] for i in 1:dim(BS), j in 1:dim(BS)] + rand_ctrl
S = BSplineManifold(ctrl, (BS, BS));
x, y, z = bspline_surf(S; M=100, N=100);
Xe, Ye, Ze = ctrl_polyhedron(ctrl);

Plot the control polyhedron as as surface, to compare its geometry with the B-spline surface, and notice that the B-spline surface "mimics" the form of the control polyhedron:

In [7]:
CV = reduce(vcat, ctrl)
figp = Plot(surface(x=reshape(CV[1:3:end], size(ctrl)), y=reshape(CV[2:3:end], size(ctrl)), 
                    z=reshape(CV[3:3:end], size(ctrl)),
                    colorscale=[[0, "#d8576b"], [1, "#d8576b"]], showscale=false,
                   ),
            fig_layout())

data: [
  "surface with fields colorscale, showscale, type, x, y, and z"
]

layout: "layout with fields font, height, margin, scene, template, and width"

In [8]:
fig3 = Plot([scatter3d(x=Xe, y=Ye, z=Ze, mode="markers+lines", marker_size=4, marker_color="#777777"),
            surface(x=x, y=y, z=z, colorbar_thickness=25, colorbar_len=0.65, 
            )],
            fig_layout())
display(fig3)

data: [
  "scatter3d with fields marker, mode, type, x, y, and z",
  "surface with fields colorbar, type, x, y, and z"
]

layout: "layout with fields font, height, margin, scene, template, and width"

### B-spline surface with simple knots

In [9]:
p = 3
knot =  KnotVector(1:9)
BS = BSplineSpace{p}(knot)
rand_ctrl = [1.2*rand(rng, 3) for i in 1:dim(BS), j in 1:dim(BS)]
ctrl = [[2*i-6.5, 2*j-6.5, -2+3*rand(rng)] for i in 1:dim(BS), j in 1:dim(BS)] + rand_ctrl
S = BSplineManifold(ctrl, (BS, BS));
x, y, z = bspline_surf(S; M=100, N=100);
Xe, Ye, Ze = ctrl_polyhedron(ctrl);
fig4 = Plot([scatter3d(x=Xe, y=Ye, z=Ze, mode="markers+lines", marker_size=4, marker_color="#777777"),
            surface(x=x, y=y, z=z, colorbar_thickness=25, colorbar_len=0.65, 
            cmin=minimum(z), cmax=maximum(z))],
            fig_layout())
display(fig4)

data: [
  "scatter3d with fields marker, mode, type, x, y, and z",
  "surface with fields cmax, cmin, colorbar, type, x, y, and z"
]

layout: "layout with fields font, height, margin, scene, template, and width"